In [144]:
import geopandas as gpd
import psycopg2
import folium
import folium.plugins
import fiona

In [145]:
import matplotlib.cm as cmx
import matplotlib.colors as colors


def rgb(minimum, maximum, value):
    minimum, maximum = float(minimum), float(maximum)
    ratio = 2 * (value-minimum) / (maximum - minimum)
    b = int(max(0, 255*(1 - ratio)))
    r = int(max(0, 255*(ratio - 1)))
    g = 255 - b - r
    return r, g, b


def style_function(feature, n_colors):
    cid = feature['properties']['cid']
    return {
        'fillOpacity': 0.5,
        'weight': 0,
        'fillColor': '#red' if cid is None else "rgb{}".format(rgb(0, n_colors, cid))
    }

def init_style_function(n_colors):
    return lambda feature: style_function(feature, n_colors)

In [146]:
rapperswil_polygon_query = "SELECT way FROM planet_osm_polygon WHERE osm_id = -1683921"
zurich_polygon_query = "SELECT way FROM planet_osm_polygon WHERE osm_id = -1682248"
switzerland_polygon_query = "SELECT way FROM planet_osm_polygon WHERE osm_id = -51701"
hombrechtikon_polygon_query = "SELECT way FROM planet_osm_polygon WHERE osm_id = -1682143"
staefa_polygon_query = "SELECT way FROM planet_osm_polygon WHERE osm_id = -1682214"

rapperswil_location = [47.226, 8.818]
zurich_location = [47.3763, 8.5403]
hombrechtikon_location = [47.25212, 8.77038]
staefa_location = [47.24062, 8.72303]

epsg = 3857

polygon_query = rapperswil_polygon_query
location = staefa_location

In [154]:
with psycopg2.connect("") as conn:
    clusters = gpd.read_postgis("SELECT hull FROM clusters;", conn, geom_col='hull')

clusters.crs = fiona.crs.from_epsg(epsg)

m = folium.Map(location=location, zoom_start=16)

folium.GeoJson(clusters).add_to(m)

m

In [283]:
points_coordinates = {
"Zürich": (47.3737, 8.5388),
"Rapperswil": (47.2269, 8.8187),
"Bern": (46.94813, 7.44656),
"Stäfa": (47.240647, 8.723481),
"Winterthur": (47.4995, 8.7258),
"Hombrechtikon": (47.2518, 8.7684),
"Basel": (47.5573, 7.5884),
"Genf": (46.2029, 6.1472),
"Rüti": (47.2582, 8.8504),
}

point_queries = {}
for name, coordinates in points_coordinates.items():
    point_queries[name] = "ST_Transform((ST_SetSRid(ST_MakePoint({}, {}), 4326)), 3857)".format(coordinates[1], coordinates[0])

current_point = "Stäfa"

query = point_queries[current_point]
location = points_coordinates[current_point]

with psycopg2.connect("") as conn:
    clusters = gpd.read_postgis("SELECT hull FROM clusters WHERE ST_Intersects(hull, {point});".format(point=query), conn, geom_col='hull')

clusters.crs = fiona.crs.from_epsg(epsg)

m = folium.Map(location=location, zoom_start=16)

folium.GeoJson(clusters).add_to(m)

m

In [285]:
eps = 35
minpoints = 3

aois_query = """
WITH hulls AS (
  SELECT hull FROM clusters WHERE ST_Intersects(hull, {point})
),
clusters AS (
  SELECT geometry,
       ST_ClusterDBSCAN(geometry, eps := {eps}, minpoints := {minpoints}) over () AS cid
  FROM pois, hulls
  WHERE ST_Within(geometry, hulls.hull)
)
SELECT * FROM clusters WHERE cid IS NOT NULL
UNION ALL
SELECT ST_ConvexHull(ST_Union(geometry)), cid FROM clusters WHERE cid IS NOT NULL GROUP BY cid
""".format(point=query, eps=eps, minpoints=minpoints)

with psycopg2.connect("") as conn:
    aois = gpd.read_postgis(aois_query, conn, geom_col='geometry')
    
n_clusters = len(aois.groupby('cid').cid.nunique())

aois.crs = fiona.crs.from_epsg(epsg)

m = folium.Map(location=location, zoom_start=15, tiles="cartodbpositron")

folium.plugins.Fullscreen().add_to(m)
folium.GeoJson(aois, style_function=init_style_function(n_clusters)).add_to(m)

m

In [278]:
import os
import gmaps
import gmaps.datasets
import geojson

gmaps.configure(api_key=os.environ["GMAPS_API_KEY"])

aois_query = """
WITH hulls AS (
  SELECT hull FROM clusters WHERE ST_Intersects(hull, {point})
),
clusters AS (
  SELECT geometry,
       ST_ClusterDBSCAN(geometry, eps := {eps}, minpoints := {minpoints}) over () AS cid
  FROM pois, hulls
  WHERE ST_Within(geometry, hulls.hull)
)
SELECT ST_ConvexHull(ST_Union(geometry)) AS geometry, cid FROM clusters WHERE cid IS NOT NULL GROUP BY cid
""".format(point=query, eps=eps, minpoints=minpoints)

with psycopg2.connect("") as conn:
    aois = gpd.read_postgis(aois_query, conn, geom_col='geometry')

aois.crs = fiona.crs.from_epsg(epsg)
aois = aois.to_crs({'init': 'epsg:4326'})

fig = gmaps.figure(center=location, zoom_level=16)
geojson_layer = gmaps.geojson_layer(geojson.loads(aois.to_json()), fill_opacity=0.01)
fig.add_layer(geojson_layer)
fig

Figure(layout=FigureLayout(height='420px'))

In [291]:
query = """
SELECT * FROM aois;
"""

with psycopg2.connect("") as conn:
    tmp = gpd.read_postgis(query, conn, geom_col='hull')
    

tmp.crs = fiona.crs.from_epsg(epsg)

m = folium.Map(location=[45.8365, 9.0293], zoom_start=16, tiles="cartodbpositron")

folium.plugins.Fullscreen().add_to(m)
folium.GeoJson(tmp).add_to(m)

m

In [292]:
tmp = tmp.to_crs({'init': 'epsg:4326'})

fig = gmaps.figure(center=location, zoom_level=16)
geojson_layer = gmaps.geojson_layer(geojson.loads(tmp.to_json()), fill_opacity=0.01)
fig.add_layer(geojson_layer)
fig

Figure(layout=FigureLayout(height='420px'))